# Reducing the energy spread in our X-band linac from 100 MeV to 500 GeV

In [ ]:
import RF_Track
import numpy
import scipy
import matplotlib.pyplot as plt

## Load the lattice from appropriate scripts

In [ ]:
import scripts

## Let's define some key parameters
We use a structure to collect all relevant parameters

In [ ]:
# Structure "setup"
class Setup:
    def __init__(self):
        self.Q = -1 # single-particle charge, in units of e
        self.mass = RF_Track.electronmass # MeV/c^2
        self.population = RF_Track.nC # 50 * RF_Track.pC; % number of real particles per bunch
        
        self.sigma_t = 0.100 # mm/c
        self.sigma_pt = 0.1 # permil, momentum spread

        self.P_i = 100 # initial momentum, MeV/c
        self.P_f = 500 # final momentum, MeV/c

        self.phid = 0 # deg, phase of the RF structures
        self.mu = 90 # deg, FODO phase advance per cell

## Let's build the linac lattice
We use a standard FODO lattice, with four structures every two consecutive quadrupoles and 90 degrees phase advance per cell

In [ ]:
setup = Setup()
rf_name = 'data/TWS_Xband.dat'
LINAC = scripts.init_linac_lattice (rf_name, setup)

In [ ]:
LINAC.size()

In [ ]:
LINAC.get_length()

## Let's define and track the reference particle

In [ ]:
P0 = scripts.init_reference_particle (setup)

# Track the reference particle
P1 = LINAC.track(P0)

In [ ]:
P1.get_phase_space()

## ...and a bunch

In [ ]:
B0 = scripts.init_bunch(rf_name, setup)

## Perform tracking

In [ ]:
B1 = LINAC.track(B0)

Let's make some plots...

In [ ]:
M0 = B0.get_phase_space ('%x %xp %y %yp %dt %P')
M1 = B1.get_phase_space ('%x %xp %y %yp %dt %P')

plt.figure()
plt.plot(M0[:,0], M0[:,1], '.', label='Initial', mfc='none')
plt.plot(M1[:,0], M1[:,1], '.', label='Final', mfc='none')
plt.xlabel('x [mm]')
plt.ylabel("x' [mrad]")

plt.figure()
plt.plot(M0[:,2], M0[:,3], '.', label='Initial', mfc='none')
plt.plot(M1[:,2], M1[:,3], '.', label='Final', mfc='none')
plt.xlabel('y [mm]')
plt.ylabel("y' [mrad]")

plt.figure()
plt.plot(M1[:,4], M1[:,5], '.', label='Final', mfc='none')
plt.xlabel('dt [mm/c]')
plt.ylabel('P [MeV/c]')
plt.tight_layout()

In [ ]:
T = LINAC.get_transport_table('%S %mean_x %mean_y')

plt.plot(T[:,0], T[:,1], linewidth=2, label='x')
plt.plot(T[:,0], T[:,2], linewidth=2, label='y')
plt.legend()
plt.xlabel('s [m]')
plt.ylabel('position [mm]')

In [ ]:
T = LINAC.get_transport_table('%S %emitt_x %emitt_y')

plt.plot(T[:,0], T[:,1], linewidth=2, label=r'$\epsilon_x$')
plt.plot(T[:,0], T[:,2], linewidth=2, label=r'$\epsilon_y$')
plt.legend()
plt.xlabel('s [m]')
plt.ylabel(r'$\epsilon_n$ [mm.mrad]')

## Intermezzo
### Fitting the transfer matrix

In [ ]:
# Transfer matrix of the linac
M0 = B0.get_phase_space('%x %xp %y %yp %dt %pt')
M1 = B1.get_phase_space('%x %xp %y %yp %dt %pt')

x0  = M0[:,0]
xp0 = M0[:,1]
y0  = M0[:,2]
yp0 = M0[:,3]
t0  = M0[:,4]
d0  = M0[:,5]

x1  = M1[:,0]
xp1 = M1[:,1]
y1  = M1[:,2]
yp1 = M1[:,3]
t1  = M1[:,4]
d1  = M1[:,5]

I = numpy.ones(x0.size)
I1 = numpy.array([x1,xp1,y1,yp1,t1,d1])
I0 = [I, # K - 0th order
      x0,xp0,y0,yp0,t0,d0 ] # R - 1st order

I0 = numpy.array(I0)

M = (numpy.linalg.pinv(I1.T)@I0.T).T
K = M[0,:]
R = M[1:7,:]

# Tracking
MT = numpy.vstack((K, R)).T
I1 = MT @ I0
print(I1)

Let's include higher orders

In [ ]:
# Transfer matrix of the linac
M0 = B0.get_phase_space('%x %xp %y %yp %dt %pt')
M1 = B1.get_phase_space('%x %xp %y %yp %dt %pt')

x0  = M0[:,0]
xp0 = M0[:,1]
y0  = M0[:,2]
yp0 = M0[:,3]
t0  = M0[:,4]
d0  = M0[:,5]

x1  = M1[:,0]
xp1 = M1[:,1]
y1  = M1[:,2]
yp1 = M1[:,3]
t1  = M1[:,4]
d1  = M1[:,5]

I = numpy.ones(x0.size)
I1 = numpy.array([x1,xp1,y1,yp1,t1,d1])
I0 = [I, # K - 0th order
      x0,xp0,y0,yp0,t0,d0, # R - 1st order
      x0**2,xp0**2,y0**2,yp0**2,t0**2*d0**2, # T 2nd-order
      x0*xp0,x0*y0,x0*yp0,x0*t0,x0*d0, # T
      xp0*y0,xp0*yp0,xp0*t0,xp0*d0, # T
      y0*yp0,y0*t0,y0*d0, # T
      yp0*t0,yp0*d0, # T
      t0*d0, # T
      d0*d0*d0,d0*d0*t0,d0*d0*x0,d0*d0*xp0,d0*d0*y0, # U - 3rd order
      d0*d0*yp0,d0*t0*t0,d0*t0*x0,d0*t0*xp0,d0*t0*y0, # U
      d0*t0*yp0,d0*x0*x0,d0*x0*xp0,d0*x0*y0,d0*x0*yp0, # U
      d0*xp0*xp0,d0*xp0*y0,d0*xp0*yp0,d0*y0*y0, # U
      d0*y0*yp0,d0*yp0*yp0,t0*t0*t0,t0*t0*x0,t0*t0*xp0, # U
      t0*t0*y0,t0*t0*yp0,t0*x0*x0,t0*x0*xp0,t0*x0*y0, # U
      t0*x0*yp0,t0*xp0*xp0,t0*xp0*y0,t0*xp0*yp0, # U
      t0*y0*y0,t0*y0*yp0,t0*yp0*yp0,x0*x0*x0,x0*x0*xp0, # U
      x0*x0*y0,x0*x0*yp0,x0*xp0*xp0,x0*xp0*y0, # U
      x0*xp0*yp0,x0*y0*y0,x0*y0*yp0,x0*yp0*yp0, # U
      xp0*xp0*xp0,xp0*xp0*y0,xp0*xp0*yp0,xp0*y0*y0, # U
      xp0*y0*yp0,xp0*yp0*yp0,y0*y0*y0,y0*y0*yp0, # U
      y0*yp0*yp0,yp0*yp0*yp0] # U
I0 = numpy.array(I0)


M = (numpy.linalg.pinv(I1.T)@I0.T).T
K = M[0,:]
R = M[1:7,:]
T = M[7:28,:]
U = M[28:,:]

# Tracking
MT = numpy.vstack((K, R, T, U)).T
I1 = MT @ I0
print(I1)

## Let's reduce the energy spread

Perform a 1D optimisation of the phase

In [ ]:
K
R
T

In [ ]:
def merit(LINAC, B0, phid):  
    # set the phase of all structures
    for rf in LINAC.get_rf_elements():
        rf.set_phid(phid)   
    # perform tracking
    B1 = LINAC.track(B0)
    I1 = B1.get_info()
    # M1 = B1.get_phase_space();
    # M = std(M1(:,6));   
    # return the momentum spread
    M = I1.sigma_pt
    # display some numbers...
    print(phid, M)
    return M
    
phid_min = scipy.optimize.fminbound(lambda x: merit(LINAC, B0, x), -30, 30)

Update the linac lattice to use the new phase

In [ ]:
setup.phid = phid_min

LINAC_1 = scripts.init_linac_lattice(rf_name, setup) #recreate the linac

In [ ]:
B1 = LINAC_1.track(B0)

In [ ]:
T = LINAC_1.get_transport_table('%S %emitt_x %emitt_y');


plt.plot(T[:,0], T[:,1], linewidth=2, label=r'$\epsilon_x$')
plt.plot(T[:,0], T[:,2], linewidth=2, label=r'$\epsilon_y$')
plt.legend()
plt.xlabel('s [m]')
plt.ylabel(r'$\epsilon_n$ [mm.mrad]')

In [ ]:
M0 = B0.get_phase_space ('%x %xp %y %yp %dt %d');
M1 = B1.get_phase_space ('%x %xp %y %yp %dt %d');

plt.figure()
plt.plot(M0[:,0], M0[:,1], '.', label='Initial', mfc='none')
plt.plot(M1[:,0], M1[:,1], '.', label='Final', mfc='none')
plt.xlabel('x [mm]')
plt.ylabel("x' [mrad]")

plt.figure()
plt.plot(M0[:,2], M0[:,3], '.', label='Initial', mfc='none')
plt.plot(M1[:,2], M1[:,3], '.', label='Final', mfc='none')
plt.xlabel('y [mm]')
plt.ylabel("y' [mrad]")

plt.figure()
plt.plot(M1[:,4], M1[:,5], '.', label='Final', mfc='none')
plt.xlabel('dt [mm/c]')
plt.ylabel('P [MeV/c]')
plt.tight_layout()